In [1]:
from torch.autograd import Function
from torch.autograd import Variable as V
import torch as t
import numpy as np
import math as m
import matplotlib.pyplot as plt
#from IPython import display
from sklearn.preprocessing import StandardScaler

In [6]:
#ifogd
class linear_regression_fractional(Function):
    def forward(ctx,w1,w2,x1,x2):
        output = w1*x1 + w2*x2
        ctx.save_for_backward(w1,w2,x1,x2,output)
        return output
    
    def backward(ctx,grad_outputs):
        w1,w2,x1,x2,output = ctx.saved_tensors
        if a==1.0:
            grad_w1 = grad_outputs*x1  #1-orde
            grad_w2 = grad_outputs*x2   #1-order
            return grad_w1,grad_w2,None,None
             
        y1 = t.where(y_pred-y <= 0, t.tensor([0.]), t.tensor([1.]))
        y_pred_f = t.abs(y_pred-y)
        grad_outputs1 = 0.5*m.gamma(3)*y_pred_f**(2-a)/m.gamma(3-a)*y1
        y2 = t.where(y_pred-y > 0, t.tensor([0.]), t.tensor([1.]))
        grad_outputs2 = (y_pred-y)*y2

        grad_outputs = 0.005*(grad_outputs1 + grad_outputs2)
        
        #w1
        if w1<=0:
            grad_w1 = grad_outputs*x1  #1-order
        else:
            grad_w1 = grad_outputs*(x1*w1**(1-a)/m.gamma(2-a)+x2*w2*w1**(-a)/m.gamma(1-a))  #fractional-order

        #w2
        if w2<=0:
            grad_w2 = grad_outputs*x2   #1-order
        else:
            grad_w2 = grad_outputs*(x1*w1*w2**(-a)/m.gamma(1-a)+x2*w2**(1-a)/m.gamma(2-a))  #fractional-order

        return grad_w1,grad_w2,None,None

In [7]:
t.manual_seed(1000) 

#random(x,y),y = 2*x - 3 + e
def get_fake_data(batch_size=200):
    x1 = t.linspace(-10,10,steps=batch_size).view(-1,1)
    x2 = t.linspace(0,20,steps=batch_size).view(-1,1)
    y = 2*x1 - 3*x2 + t.normal(0,5,size=(batch_size, 1))
    return x1,x2, y

In [44]:
a = 1.5   #alpha,0.1,0.3,0.5,0.7,0.9,1.0,1.1,1.3,1.5

#position10
#w1 = V(t.tensor([-1.]), requires_grad=True)  #initial w1
#w2 = V(t.tensor([-1.]), requires_grad=True)  #initial w2

#position11
#w1 = V(t.tensor([5.]), requires_grad=True)  #initial w1
#w2 = V(t.tensor([-1.]), requires_grad=True)  #initial w2

#position12
#w1 = V(t.tensor([5.]), requires_grad=True)  #initial w1
#w2 = V(t.tensor([-5.]), requires_grad=True)  #initial w2

#position13
w1 = V(t.tensor([-1.]), requires_grad=True)  #initial w1
w2 = V(t.tensor([-5.]), requires_grad=True)  #initial w2

lr =1e-3 # learning rate

#trajectory of IFOGD in different alpha
#ifogd_w1_15_0,ifogd_w2_15_0 = [],[]    #alpha,0.1,0.3,0.5,0.7,0.9,1.0,1.1,1.3,1.5
#ifogd_w1_15_1,ifogd_w2_15_1 = [],[]
#ifogd_w1_15_2,ifogd_w2_15_2 = [],[]
ifogd_w1_15_3,ifogd_w2_15_3 = [],[]


for ii in range(300):
    x1,x2, y = get_fake_data()
    x1,x2, y = V(x1),V(x2), V(y)

    y_pred = linear_regression_fractional.apply(w1,w2,x1,x2)   #IFOGD
    loss = 0.5 * (y_pred - y)** 2
    loss = loss.mean()  
    
    loss.backward()  #fractional order grad
    
    #record0
    #ifogd_w1_15_0.append(float(w1.data))   #alpha,0.1,0.3,0.5,0.7,0.9,1.0,1.1,1.3,1.5
    #ifogd_w2_15_0.append(float(w2.data))
    
    #record1
    #ifogd_w1_15_1.append(float(w1.data))  
    #ifogd_w2_15_1.append(float(w2.data))
    
    #record2
    #ifogd_w1_15_2.append(float(w1.data))
    #ifogd_w2_15_2.append(float(w2.data))

    #record3
    ifogd_w1_15_3.append(float(w1.data))
    ifogd_w2_15_3.append(float(w2.data))
    
    
    w1.data.sub_(lr * w1.grad.data)
    w2.data.sub_(lr * w2.grad.data)
    
    w1.grad.data.zero_()
    w2.grad.data.zero_()

In [46]:
fig = plt.figure(figsize=(10,8),dpi=1200)
custom_params = {
    'font.size': 10,
    'lines.linewidth': 0.1,
    'axes.labelsize': 10,
    'axes.titlesize': 10,
    'xtick.labelsize': 10,
    'ytick.labelsize': 10,
    'legend.fontsize': 8,
    'grid.linestyle': '--',
    'grid.alpha': 0.7,
}

plt.rcParams.update(custom_params)
fig.subplots_adjust(wspace=0, hspace=0) 
step = 0.01
x = np.arange(-2,6,step)
y = np.arange(-6,0,step)
X,Y = np.meshgrid(x,y)
Z = (X-2)**2+(Y+3)**2

ax1 = fig.add_subplot(3, 3, 1)
ax1.contour(X,Y,Z,10,linewidth = 0.1)
ax1.plot(ifogd_w1_01_0,ifogd_w2_01_0,'o-',markersize='1',linewidth='0.5')
ax1.annotate(r'$( - 1, - 1)$', xy=(-1.8,-0.7))
ax1.plot(ifogd_w1_01_1,ifogd_w2_01_1,'o-',markersize='1',linewidth='0.5')
ax1.annotate(r'$( 5, - 1)$', xy=(4,-0.7))
ax1.plot(ifogd_w1_01_2,ifogd_w2_01_2,'o-',markersize='1',linewidth='0.5')
ax1.annotate(r'$( 5, -5)$', xy=(4,-5.5))
ax1.plot(ifogd_w1_01_3,ifogd_w2_01_3,'o-',markersize='1',linewidth='0.5')
ax1.annotate(r'$( -1, - 5)$', xy=(-1.8,-5.5))
ax1.set_xlim(-2,6)
ax1.set_ylim(-6,0)
ax1.set_yticklabels([-6,-5,-4,-3,-2,-1,0])
ax1.set_title(r'$\alpha  = 0.1,IFOGD$',bbox=dict(facecolor='y', edgecolor='blue', alpha=0.65 ),x=0.5,y=0.7,fontsize='8')

ax2 = fig.add_subplot(3, 3, 2)
ax2.contour(X,Y,Z,10,linewidth = 0.1)
ax2.plot(ifogd_w1_03_0,ifogd_w2_03_0,'o-',markersize='1',linewidth='0.5')
ax2.annotate(r'$( - 1, - 1)$', xy=(-1.8,-0.7))
ax2.plot(ifogd_w1_03_1,ifogd_w2_03_1,'o-',markersize='1',linewidth='0.5')
ax2.annotate(r'$( 5, - 1)$', xy=(4,-0.7))
ax2.plot(ifogd_w1_03_2,ifogd_w2_03_2,'o-',markersize='1',linewidth='0.5')
ax2.annotate(r'$( 5, -5)$', xy=(4,-5.5))
ax2.plot(ifogd_w1_01_3,ifogd_w2_03_3,'o-',markersize='1',linewidth='0.5')
ax2.annotate(r'$( -1, - 5)$', xy=(-1.8,-5.5))
ax2.set_xlim(-2,6)
ax2.set_ylim(-6,0)
ax2.set_xticklabels([])
ax2.set_yticklabels([])
ax2.set_title(r'$\alpha  = 0.3,IFOGD$',bbox=dict(facecolor='y', edgecolor='blue', alpha=0.65 ),x=0.5,y=0.7,fontsize='8')

ax3 = fig.add_subplot(3, 3, 3)
ax3.contour(X,Y,Z,10,linewidth = 0.1)
ax3.plot(ifogd_w1_05_0,ifogd_w2_05_0,'o-',markersize='1',linewidth='0.5')
ax3.annotate(r'$( - 1, - 1)$', xy=(-1.8,-0.7))
ax3.plot(ifogd_w1_05_1,ifogd_w2_05_1,'o-',markersize='1',linewidth='0.5')
ax3.annotate(r'$( 5, - 1)$', xy=(4,-0.7))
ax3.plot(ifogd_w1_05_2,ifogd_w2_05_2,'o-',markersize='1',linewidth='0.5')
ax3.annotate(r'$( 5, -5)$', xy=(4,-5.5))
ax3.plot(ifogd_w1_05_3,ifogd_w2_05_3,'o-',markersize='1',linewidth='0.5')
ax3.annotate(r'$( -1, - 5)$', xy=(-1.8,-5.5))
ax3.set_xlim(-2,6)
ax3.set_ylim(-6,0)
ax3.set_xticklabels([])
ax3.set_yticklabels([])
ax3.set_title(r'$\alpha  = 0.5,IFOGD$',bbox=dict(facecolor='y', edgecolor='blue', alpha=0.65 ),x=0.5,y=0.7,fontsize='8')

ax4 = fig.add_subplot(3, 3, 4)
ax4.contour(X,Y,Z,10,linewidth = 0.1)
ax4.plot(ifogd_w1_07_0,ifogd_w2_07_0,'o-',markersize='1',linewidth='0.5')
ax4.annotate(r'$( - 1, - 1)$', xy=(-1.8,-0.7))
ax4.plot(ifogd_w1_07_1,ifogd_w2_07_1,'o-',markersize='1',linewidth='0.5')
ax4.annotate(r'$( 5, - 1)$', xy=(4,-0.7))
ax4.plot(ifogd_w1_07_2,ifogd_w2_07_2,'o-',markersize='1',linewidth='0.5')
ax4.annotate(r'$( 5, -5)$', xy=(4,-5.5))
ax4.plot(ifogd_w1_07_3,ifogd_w2_07_3,'o-',markersize='1',linewidth='0.5')
ax4.annotate(r'$( -1, - 5)$', xy=(-1.8,-5.5))
ax4.set_xlim(-2,6)
ax4.set_ylim(-6,0)
ax4.set_xticklabels([])
ax4.set_yticklabels([-6,-5,-4,-3,-2,-1,])
ax4.set_title(r'$\alpha  = 0.7,IFOGD$',bbox=dict(facecolor='y', edgecolor='blue', alpha=0.65 ),x=0.5,y=0.7,fontsize='8')

ax5 = fig.add_subplot(3, 3, 5)
ax5.contour(X,Y,Z,10,linewidth = 0.1)
ax5.plot(ifogd_w1_09_0,ifogd_w2_09_0,'o-',markersize='1',linewidth='0.5')
ax5.annotate(r'$( - 1, - 1)$', xy=(-1.8,-0.7))
ax5.plot(ifogd_w1_09_1,ifogd_w2_09_1,'o-',markersize='1',linewidth='0.5')
ax5.annotate(r'$( 5, - 1)$', xy=(4,-0.7))
ax5.plot(ifogd_w1_09_2,ifogd_w2_09_2,'o-',markersize='1',linewidth='0.5')
ax5.annotate(r'$( 5, -5)$', xy=(4,-5.5))
ax5.plot(ifogd_w1_09_3,ifogd_w2_09_3,'o-',markersize='1',linewidth='0.5')
ax5.annotate(r'$( -1, - 5)$', xy=(-1.8,-5.5))
ax5.set_xlim(-2,6)
ax5.set_ylim(-6,0)
ax5.set_xticklabels([])
ax5.set_yticklabels([])
ax5.set_title(r'$\alpha  = 0.9,IFOGD$',bbox=dict(facecolor='y', edgecolor='blue', alpha=0.65 ),x=0.5,y=0.7,fontsize='8')

ax6 = fig.add_subplot(3, 3, 6)
ax6.contour(X,Y,Z,10,linewidth = 0.1)
ax6.plot(ifogd_w1_10_0,ifogd_w2_10_0,'o-',markersize='1',linewidth='0.5')
ax6.annotate(r'$( - 1, - 1)$', xy=(-1.8,-0.7))
ax6.plot(ifogd_w1_10_1,ifogd_w2_10_1,'o-',markersize='1',linewidth='0.5')
ax6.annotate(r'$( 5, - 1)$', xy=(4,-0.7))
ax6.plot(ifogd_w1_10_2,ifogd_w2_10_2,'o-',markersize='1',linewidth='0.5')
ax6.annotate(r'$( 5, -5)$', xy=(4,-5.5))
ax6.plot(ifogd_w1_10_3,ifogd_w2_10_3,'o-',markersize='1',linewidth='0.5')
ax6.annotate(r'$( -1, - 5)$', xy=(-1.8,-5.5))
ax6.set_xlim(-2,6)
ax6.set_ylim(-6,0)
ax6.set_xticklabels([])
ax6.set_yticklabels([])
ax6.set_title(r'$\alpha  = 1.0,IFOGD$',bbox=dict(facecolor='y', edgecolor='blue', alpha=0.65 ),x=0.55,y=0.7,fontsize='8')

ax7 = fig.add_subplot(3, 3, 7)
ax7.contour(X,Y,Z,10,linewidth = 0.1)
ax7.plot(ifogd_w1_11_0,ifogd_w2_11_0,'o-',markersize='1',linewidth='0.5')
ax7.annotate(r'$( - 1, - 1)$', xy=(-1.8,-0.7))
ax7.plot(ifogd_w1_11_1,ifogd_w2_11_1,'o-',markersize='1',linewidth='0.5')
ax7.annotate(r'$( 5, - 1)$', xy=(4,-0.7))
ax7.plot(ifogd_w1_11_2,ifogd_w2_11_2,'o-',markersize='1',linewidth='0.5')
ax7.annotate(r'$( 5, -5)$', xy=(4,-5.5))
ax7.plot(ifogd_w1_11_3,ifogd_w2_11_3,'o-',markersize='1',linewidth='0.5')
ax7.annotate(r'$( -1, - 5)$', xy=(-1.8,-5.5))
ax7.set_xlim(-2,6)
ax7.set_ylim(-6,0)
ax7.set_xticklabels([-2,0,2,4,])
ax7.set_yticklabels([-6,-5,-4,-3,-2,-1,])
ax7.set_title(r'$\alpha  = 1.1,IFOGD$',bbox=dict(facecolor='y', edgecolor='blue', alpha=0.65 ),x=0.5,y=0.7,fontsize='8')

ax8 = fig.add_subplot(3, 3, 8)
ax8.contour(X,Y,Z,10,linewidth = 0.1)
ax8.plot(ifogd_w1_13_0,ifogd_w2_13_0,'o-',markersize='1',linewidth='0.5')
ax8.annotate(r'$( - 1, - 1)$', xy=(-1.8,-0.7))
ax8.plot(ifogd_w1_13_1,ifogd_w2_13_1,'o-',markersize='1',linewidth='0.5')
ax8.annotate(r'$( 5, - 1)$', xy=(4,-0.7))
ax8.plot(ifogd_w1_13_2,ifogd_w2_13_2,'o-',markersize='1',linewidth='0.5')
ax8.annotate(r'$( 5, -5)$', xy=(4,-5.5))
ax8.plot(ifogd_w1_13_3,ifogd_w2_13_3,'o-',markersize='1',linewidth='0.5')
ax8.annotate(r'$( -1, - 5)$', xy=(-1.8,-5.5))
ax8.set_xlim(-2,6)
ax8.set_ylim(-6,0)
ax8.set_yticklabels([])
ax8.set_xticklabels([-2,0,2,4,])
ax8.set_title(r'$\alpha  = 1.3,IFOGD$',bbox=dict(facecolor='y', edgecolor='blue', alpha=0.65 ),x=0.5,y=0.7,fontsize='8')

ax9 = fig.add_subplot(3, 3, 9)
ax9.contour(X,Y,Z,10,linewidth = 0.1)
ax9.plot(ifogd_w1_15_0,ifogd_w2_15_0,'o-',markersize='1',linewidth='0.5')
ax9.annotate(r'$( - 1, - 1)$', xy=(-1.8,-0.7))
ax9.plot(ifogd_w1_15_1,ifogd_w2_15_1,'o-',markersize='1',linewidth='0.5')
ax9.annotate(r'$( 5, - 1)$', xy=(4,-0.7))
ax9.plot(ifogd_w1_15_2,ifogd_w2_15_2,'o-',markersize='1',linewidth='0.5')
ax9.annotate(r'$( 5, -5)$', xy=(4,-5.5))
ax9.plot(ifogd_w1_15_3,ifogd_w2_15_3,'o-',markersize='1',linewidth='0.5')
ax9.annotate(r'$( -1, - 5)$', xy=(-1.8,-5.5))
ax9.set_xlim(-2,6)
ax9.set_ylim(-6,0)
ax9.set_yticklabels([])
ax9.set_xticklabels([-2,0,2,4,6])
ax9.set_title(r'$\alpha  = 1.5,IFOGD$',bbox=dict(facecolor='y', edgecolor='blue', alpha=0.65 ),x=0.5,y=0.7,fontsize='8')

ax8.set_xlabel(r'${w_1}$',fontsize='15')
ax4.set_ylabel(r'${w_2}$',fontsize='15')
plt.savefig('picture/Fig5.eps',bbox_inches='tight',format='eps')
plt.savefig('picture/Fig5.svg',bbox_inches='tight',format='svg')
plt.savefig('picture/Fig5.pdf',bbox_inches='tight',format='pdf')
plt.show()

C:\Users\1508-T3630\AppData\Local\Temp\ipykernel_14376\4192592331.py:23: UserWarning: The following kwargs were not used by contour: 'linewidth'
  ax1.contour(X,Y,Z,10,linewidth = 0.1)
C:\Users\1508-T3630\AppData\Local\Temp\ipykernel_14376\4192592331.py:34: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax1.set_yticklabels([-6,-5,-4,-3,-2,-1,0])
C:\Users\1508-T3630\AppData\Local\Temp\ipykernel_14376\4192592331.py:38: UserWarning: The following kwargs were not used by contour: 'linewidth'
  ax2.contour(X,Y,Z,10,linewidth = 0.1)
C:\Users\1508-T3630\AppData\Local\Temp\ipykernel_14376\4192592331.py:54: UserWarning: The following kwargs were not used by contour: 'linewidth'
  ax3.contour(X,Y,Z,10,linewidth = 0.1)
C:\Users\1508-T3630\AppData\Local\Temp\ipykernel_14376\4192592331.py:70: UserWarning: The following kwargs were not used by contour: 'linewidth'
  ax4.contour(X,Y,Z,10,linewidth = 0.1)
C:\Users\1508-T3630\AppData\Local\Temp\ipykernel_14376\4192592331.p